In [68]:
# -*- coding: utf-8 -*-
from bs4 import BeautifulSoup
import time
import random
import re
from tqdm import tqdm
import pandas as pd
import numpy as np
import time
import requests
import sys
import json
import pickle
from itertools import combinations

from konlpy.tag import Komoran

# bigram 생성에 필요한 library
from gensim.models import Phrases
from gensim.models.phrases import Phraser

# vectorize & lda에 필요한 library
from gensim import corpora
from gensim.models.ldamodel import LdaModel

# gensim의 ldamodel에 최적화된 라이브러리
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis  

In [69]:
with open('./final_model/all_contents_refined_dup.pickle', 'rb') as f:
    all_contents_refined = pickle.load(f)
    
with open('./final_model/corpus.pickle', 'rb') as f:
    corpus = pickle.load(f)
    
with open('./final_model/dictionary.pickle', 'rb') as f:
    dictionary = pickle.load(f)
    
with open('./final_model/merged.pickle', 'rb') as f:
    merged = pickle.load(f)
    
with open('./final_model/topic6_dict.pickle', 'rb') as f:
    topic6_dict = pickle.load(f)

In [71]:
model_saved = LdaModel.load('./final_model/final_model_pass80.atmodel')

In [72]:
contents_index=all_contents_refined['idx']
all_comments_refined = [x for x,idx in zip(merged['comments'],range(len(merged['comments']))) if idx in contents_index]
all_titles_refined = [x for x,idx in zip(merged['titles'],range(len(merged['titles']))) if idx in contents_index]
all_urls_refined = [x for x,idx in zip(merged['urls'],range(len(merged['urls']))) if idx in contents_index]

In [75]:
topic6_dict=dict()
for i in range(6):
    topic6_dict[i]={'titles':[],
                   'contents':[],
                   'comments':[],
                   'similarity':[],
                   'idx':[]}

In [76]:
def make_topictable_per_doc(ldamodel, corpus):
    topic_table = pd.DataFrame()

    for i, topic_list in enumerate(ldamodel[corpus]):
        doc = topic_list[0] if ldamodel.per_word_topics else topic_list            
        doc = sorted(doc, key=lambda x: (x[1]), reverse=True)

        for j, (topic_num, prop_topic) in enumerate(doc): 
            if j == 0:  
                topic_table = topic_table.append(pd.Series([int(topic_num), round(prop_topic,4), topic_list]), ignore_index=True)
            else:
                break
    return(topic_table)

In [78]:
topictable = make_topictable_per_doc(model_saved, corpus)
topictable = topictable.reset_index() 
topictable.columns = ['No_document', 'No_topic', 'similarity', 'detail']

In [82]:
for idx,row in topictable.iterrows():
    topic6_dict[int(row['No_topic'])]['titles'].append(all_titles_refined[idx])
    topic6_dict[int(row['No_topic'])]['contents'].append(all_contents_refined['contents'][idx])
    topic6_dict[int(row['No_topic'])]['comments'].append(all_comments_refined[idx])
    topic6_dict[int(row['No_topic'])]['similarity'].append(row['similarity'])
    topic6_dict[int(row['No_topic'])]['idx'].append(idx)

In [83]:
topic6_dict

{0: {'titles': ['"전동킥체어?" 한문철 변호사도 처음 보는 교통수단이 등장했다',
   "하남시, '방치 공유 전동킥보드 신고' 카톡 오픈채팅방 개설",
   '‘킥보드 수거 좀...’ 5개월새 신고 3만건',
   '세종시 "전동 킥보드, 안전한 곳에 주차해 주세요"',
   '동작구, 방치 전동킥보드 견인…5개월만에 1600건 돌파',
   '[단독] 청사포~오시리아 전동킥보드 전용도로 만들자',
   '동작구, 방치 전동킥보드 견인…5개월만에 1600건 넘어',
   '해운대 \'전동킥보드 전용도로\' 추진…"바다 보러 퍼뜩 오이소"',
   '[마부작침] 킥보드, 어디로 다니란 말인가?',
   '[마부작침] 강남에서 전동킥보드 타기…안전하다? 아니다?',
   '한 달에 평균 3,000건 견인…내던져진 킥보드 어떡하나',
   '[풀뿌리K] 주민의 조용한 정치혁명…“견제와 독려를”',
   '파리 관광지에서 전동 킥보드로 과속 못한다…10㎞/h 제한',
   '길거리에 방치된 전동 킥보드…강서구도 11월부터 견인',
   '[마부작침] 네 달 동안 1만 1,996건 공유킥보드 불법 주차, 방법 없나?',
   '독일, 버려지는 전동 킥보드로 환경오염 우려',
   '인도 막은 ‘민폐’ 전동 킥보드…“견인합니다”',
   '[이슈 컷] 시나브로 철수하는 공유 킥보드…왜?',
   "노량진역·보라매공원 '불법 주차' 전동 킥보드 15일부터 견인",
   '송파, 방치된 전동 킥보드 발견 즉시 견인',
   "'전동 킥보드' 시골 도심거리도 잠식",
   '킥보드 길거리\xa0골칫덩어리?...견인에 시민반색·업계 한숨',
   '노원구, 전동킥보드 불법주정차 스마트폰 신고 시스템 구축',
   '“전동 킥보드 빌려줄 때 안전장비도 함께 대여를”',
   '성동, 보도에 방치된 전동 킥보드 견인',
   '"점자블록 위에 킥보드, 누군가의 생명 위협합니다"',
   '정류장 주변에 전동 킥보드 주차공간 생긴다',
   "대구, 무단방치 킥보드 